In [23]:
#Baseline Parameters
C_m  =   1.0
#membrane capacitance, in uF/cm^2"""
g_Na = 120.0
#Sodium (Na) maximum conductances, in mS/cm^2"""
g_K  =  36.0
#Postassium (K) maximum conductances, in mS/cm^2"""
g_L  =   0.3
#Leak maximum conductances, in mS/cm^2"""
E_Na =  50.0
#Sodium (Na) Nernst reversal potentials, in mV"""
E_K  = -77.0
#Postassium (K) Nernst reversal potentials, in mV"""
E_L  = -54.387
#Leak channels Nernst reversal potentials, in mV"""

-54.387

In [24]:
using ODE
using PyCall
# PyCall package to call Scipy integrate function
@pyimport scipy.integrate as si

In [25]:
# Time steps
step = collect(range(0,0.01,45000))

45000-element Array{Float64,1}:
   0.0 
   0.01
   0.02
   0.03
   0.04
   0.05
   0.06
   0.07
   0.08
   0.09
   0.1 
   0.11
   0.12
   ⋮   
 449.88
 449.89
 449.9 
 449.91
 449.92
 449.93
 449.94
 449.95
 449.96
 449.97
 449.98
 449.99

In [26]:
#Channel Dynamics functions
alpha_m(V) = 0.1*(V+40.0)/(1.0 - exp(-(V+40.0) / 10.0))

alpha_m (generic function with 1 method)

In [27]:
beta_m(V) =  4.0 * exp(-(V+65.0) / 18.0)

beta_m (generic function with 1 method)

In [28]:
alpha_h(V) = 0.07 * exp(-(V+65.0) / 20.0)

alpha_h (generic function with 1 method)

In [29]:
beta_h(V) = 1.0/(1.0 + exp(-(V+35.0) / 10.0))

beta_h (generic function with 1 method)

In [30]:
alpha_n(V) = 0.01*(V+55.0)/(1.0 - exp(-(V+55.0) / 10.0))

alpha_n (generic function with 1 method)

In [31]:
beta_n(V) = 0.125 * exp(-(V+65) / 80.0)

beta_n (generic function with 1 method)

In [32]:
# To Calculate Inhibitory Sodium current 
I_Na(V, m, h) = g_Na * m^3 * h * (V - E_Na)

I_Na (generic function with 1 method)

In [33]:
# To Calculate Inhibitory Potassium current 
I_K(V, n) = g_K  * n^4 * (V - E_K)

I_K (generic function with 1 method)

In [34]:
# To Calculate Inhibitory Leak current 
I_L(V) = g_L * (V - E_L)

I_L (generic function with 1 method)

In [35]:
function fcheck(x,t)
    if t > x
        return 1
    else
        return 0
    end
end
    

fcheck (generic function with 1 method)

In [36]:
I_inj(t) = 10*(fcheck(100,t)) - 10*(fcheck(200,t)) + 35*(fcheck(300,t)) - 35*(fcheck(400,t))

I_inj (generic function with 1 method)

In [37]:
function dALLdt(X,t)
    V,m,h,n = X 
    dVdt = (I_inj(t) - I_Na(V, m, h) - I_K(V, n) - I_L(V)) / C_m
    dmdt = alpha_m(V)*(1.0-m) - beta_m(V)*m
    dhdt = alpha_h(V)*(1.0-h) - beta_h(V)*h
    dndt = alpha_n(V)*(1.0-n) - beta_n(V)*n
#    println(I_inj(t))
#    print(I_Na(V,m,h))
#    print(I_K(V,n))
#    print(I_L(V))
#    print(t+"\t"+I_inj(t)+"\t"+I_Na(V, m, h)+"\t"+I_K(V, n)+"\t"+I_L(V)+"\t"+C_m+"\t"+V+"\t"+m+"\t"+h+"\t"+n+"\t"+alpha_m(V)+"\t"+alpha_h(V)+"\t"+alpha_n(V)+"\t"+beta_m(V)+"\t"+beta_h(V)+"\t"+beta_n(V)+"\t"+dVdt+"\t"+dmdt+"\t"+dhdt+"\t"+dndt)  
#    print(dVdt)
#    print(dmdt)
#    print(dhdt)
#    print(dndt)
#    print("\n")
    return dVdt, dmdt, dhdt, dndt
end

dALLdt (generic function with 1 method)

In [ ]:
#t,y = ODE.ode23s(dALLdt,[-65, 0.05, 0.6, 0.32],step)
y = [[]]
y = si.odeint(dALLdt, [-65, 0.05, 0.6, 0.32],step)

-0.310948320000000060.012385538355398518-0.0004555239065400646-0.00042558393288580354
-0.31094709207316250.012385464723561723-0.00045552228095895736-0.0004255849017167912
-0.310947092079699060.012385464723979778-0.0004555222809653238-0.0004255849017124058
-0.310945864158836740.012385391092558873-0.0004555206553906524-0.00042558587053894564
-0.31094586416537460.012385391092976927-0.00045552065539701883-0.0004255858705345533
-0.30477264053994490.012015956091539298-0.00044732875178042295-0.0004304603202437071
-0.30477144258416810.012015879150134245-0.0004473277307950607-0.00043046102848175866
-0.298750688935505160.01165699952118579-0.0004392991595929055-0.0004352227425125435
-0.298748318178257750.011656847659082814-0.00043929713733088446-0.0004352241452813266
-0.29287543059894670.011308154452173619-0.000431426891783087-0.00043987659066085927
-0.292873117975149370.011308006705264467-0.00043142491494928617-0.0004398779618906973
-0.277654882425232060.010410896480966603-0.000410833865045087-0

In [43]:
using Plots

In [51]:
Vh = y[:,1]
mh = y[:,2]
hh = y[:,3]
nh = y[:,4]

45000-element Array{Float64,1}:
 0.32    
 0.319996
 0.319991
 0.319987
 0.319982
 0.319978
 0.319973
 0.319968
 0.319964
 0.319959
 0.319954
 0.319949
 0.319944
 ⋮       
 0.317727
 0.317727
 0.317727
 0.317727
 0.317727
 0.317727
 0.317727
 0.317727
 0.317727
 0.317727
 0.317727
 0.317727

In [105]:
# To calculate inhibitory currents for Sodium channel, Potassium channel and Leak currents
xlen = length(Vh)
iNa = Array(Float64,45000) 
iK = Array(Float64,45000) 
iNa = fill(0.0,45000)
iK = fill(0.0,45000)
iL = I_L(Vh)                            # Leak Current
for i = 1:45000
    iNa[i] = I_Na(Vh[i], mh[i], hh[i])  # for Sodium channel
    iK[i] = I_K(Vh[i],nh[i])            # for Potassium channel
end


In [114]:
plot(Vh,label = "V")

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 10000 
 
 
 20000 
 
 
 30000 
 
 
 40000 
 
 
 -50 
 
 
 0 
 
<polyline clip-path="url(#clip02)" style="stroke:#0099ff; stroke-width:0.8; stroke-opacity:1; fill:none" points="
 30.6037,349.499 30.6162,349.509 30.6288,349.518 30.6414,349.528 30.6539,349.537 30.6665,349.545 30.6791,349.554 30.6916,349.562 30.7042,349.57 30.7168,349.577 
 30.7293,349.585 30.7419,349.592 30.7545,349.599 30.767,349.606 30.7796,349.613 30.7922,349.619 30.8047,349.625 30.8173,349.632 30.8299,349.637 30.8424,349.643 
 30.855,349.649 30.8676,349.654 30.8801,349.66 30.8927,349.665 30.9053,349.67 30.9178,349.675 30.9304,349.68 30.943,349.685 30.9555,349.689 30.9681,349.694 
 30.9807,349.698 30.9932,349.703 31.0058,349.707 31.0184,349.711 31.0309,349.715 31.0435,349.719 31.0561,349.723 31.0686,349.727 31.0812,349.73 31.0938,349.734 
 31.1063,349.738 31.1189,349.741 31.1314,349.745 31.144,349.748 31.1566,349.752 31.1691,349.755 31.1817,349.758 31.1943,349.761 31.2068,349.764 31.2194,349.767 
 31.232,349.77 31.2445,349.773 31.2571,349.776 31.2697,349.779 31.2822,349.782 31.2948,349.785 31.3074,349.788 31.3199,349.79 31.3325,349.793 31.3451,349.796 
 31.3576,349.798 31.3702,349.801 31.3828,349.803 31.3953,349.806 31.4079,349.808 31.4205,349.811 31.433,349.813 31.4456,349.816 31.4582,349.818 31.4707,349.82 
 31.4833,349.822 31.4959,349.825 31.5084,349.827 31.521,349.829 31.5336,349.831 31.5461,349.833 31.5587,349.836 31.5713,349.838 31.5838,349.84 31.5964,349.842 
 31.609,349.844 31.6215,349.846 31.6341,349.848 31.6467,349.85 31.6592,349.852 31.6718,349.854 31.6844,349.856 31.6969,349.857 31.7095,349.859 31.7221,349.861 
 31.7346,349.863 31.7472,349.865 31.7598,349.867 31.7723,349.868 31.7849,349.87 31.7974,349.872 31.81,349.873 31.8226,349.875 31.8351,349.877 31.8477,349.878 
 31.8603,349.88 31.8728,349.882 31.8854,349.883 31.898,349.885 31.9105,349.886 31.9231,349.888 31.9357,349.89 31.9482,349.891 31.9608,349.893 31.9734,349.894 
 31.9859,349.895 31.9985,349.897 32.0111,349.898 32.0236,349.9 32.0362,349.901 32.0488,349.903 32.0613,349.904 32.0739,349.905 32.0865,349.907 32.099,349.908 
 32.1116,349.909 32.1242,349.911 32.1367,349.912 32.1493,349.913 32.1619,349.914 32.1744,349.916 32.187,349.917 32.1996,349.918 32.2121,349.919 32.2247,349.92 
 32.2373,349.922 32.2498,349.923 32.2624,349.924 32.275,349.925 32.2875,349.926 32.3001,349.927 32.3127,349.928 32.3252,349.929 32.3378,349.93 32.3504,349.931 
 32.3629,349.932 32.3755,349.933 32.3881,349.934 32.4006,349.935 32.4132,349.936 32.4258,349.937 32.4383,349.938 32.4509,349.939 32.4634,349.94 32.476,349.941 
 32.4886,349.942 32.5011,349.943 32.5137,349.944 32.5263,349.945 32.5388,349.945 32.5514,349.946 32.564,349.947 32.5765,349.948 32.5891,349.949 32.6017,349.949 
 32.6142,349.95 32.6268,349.951 32.6394,349.952 32.6519,349.952 32.6645,349.953 32.6771,349.954 32.6896,349.955 32.7022,349.955 32.7148,349.956 32.7273,349.957 
 32.7399,349.957 32.7525,349.958 32.765,349.958 32.7776,349.959 32.7902,349.96 32.8027,349.96 32.8153,349.961 32.8279,349.961 32.8404,349.962 32.853,349.962 
 32.8656,349.963 32.8781,349.964 32.8907,349.964 32.9033,349.965 32.9158,349.965 32.9284,349.965 32.941,349.966 32.9535,349.966 32.9661,349.967 32.9787,349.967 
 32.9912,349.968 33.0038,349.968 33.0164,349.968 33.0289,349.969 33.0415,349.969 33.0541,349.97 33.0666,349.97 33.0792,349.97 33.0918,349.971 33.1043,349.971 
 33.1169,349.971 33.1294,349.971 33.142,349.972 33.1546,349.972 33.1671,349.972 33.1797,349.973 33.1923,349.973 33.2048,349.973 33.2174,349.973 33.23,349.973 
 33.2425,349.974 33.2551,349.974 33.2677,349.974 33.2802,349.974 33.2928,349.974 33.3054,349.975 33.3179,349.975 33.3305,349.975 33.3431,349.975 33.3556,349.975 
 33.3682,349.975 33.3808,349.975 33.3933,349.975 33.4059,349.975 33.4185,349.975 33.431,349.975 33.4436,349.976 33.4562,349.976 33.4687,349.976 33.4813,349.976 
 33.4939,349.976 33.5064,349.976 33.51

In [125]:
plot(mh,label = "m")
plot!(hh,label = "h")
plot!(nh,label = "n")

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 10000 
 
 
 20000 
 
 
 30000 
 
 
 40000 
 
 
 0.25 
 
 
 0.50 
 
 
 0.75 
 
<polyline clip-path="url(#clip02)" style="stroke:#0099ff; stroke-width:0.8; stroke-opacity:1; fill:none" points="
 39.4926,370.898 39.5049,370.851 39.5173,370.806 39.5297,370.764 39.542,370.723 39.5544,370.685 39.5668,370.648 39.5791,370.613 39.5915,370.58 39.6039,370.548 
 39.6162,370.518 39.6286,370.489 39.641,370.462 39.6534,370.436 39.6657,370.412 39.6781,370.388 39.6905,370.366 39.7028,370.345 39.7152,370.325 39.7276,370.306 
 39.7399,370.288 39.7523,370.271 39.7647,370.254 39.777,370.239 39.7894,370.224 39.8018,370.21 39.8141,370.197 39.8265,370.185 39.8389,370.173 39.8513,370.162 
 39.8636,370.151 39.876,370.141 39.8884,370.132 39.9007,370.123 39.9131,370.114 39.9255,370.106 39.9378,370.099 39.9502,370.092 39.9626,370.085 39.9749,370.079 
 39.9873,370.073 39.9997,370.068 40.012,370.062 40.0244,370.057 40.0368,370.053 40.0491,370.049 40.0615,370.045 40.0739,370.041 40.0863,370.037 40.0986,370.034 
 40.111,370.031 40.1234,370.028 40.1357,370.026 40.1481,370.023 40.1605,370.021 40.1728,370.019 40.1852,370.017 40.1976,370.016 40.2099,370.014 40.2223,370.013 
 40.2347,370.011 40.247,370.01 40.2594,370.009 40.2718,370.008 40.2841,370.008 40.2965,370.007 40.3089,370.006 40.3213,370.006 40.3336,370.005 40.346,370.005 
 40.3584,370.005 40.3707,370.005 40.3831,370.005 40.3955,370.005 40.4078,370.005 40.4202,370.005 40.4326,370.005 40.4449,370.006 40.4573,370.006 40.4697,370.006 
 40.482,370.007 40.4944,370.007 40.5068,370.008 40.5191,370.008 40.5315,370.009 40.5439,370.009 40.5563,370.01 40.5686,370.011 40.581,370.012 40.5934,370.012 
 40.6057,370.013 40.6181,370.014 40.6305,370.015 40.6428,370.015 40.6552,370.016 40.6676,370.017 40.6799,370.018 40.6923,370.019 40.7047,370.02 40.717,370.021 
 40.7294,370.022 40.7418,370.023 40.7542,370.024 40.7665,370.025 40.7789,370.026 40.7913,370.027 40.8036,370.028 40.816,370.029 40.8284,370.03 40.8407,370.031 
 40.8531,370.032 40.8655,370.033 40.8778,370.034 40.8902,370.035 40.9026,370.036 40.9149,370.037 40.9273,370.038 40.9397,370.039 40.952,370.04 40.9644,370.041 
 40.9768,370.042 40.9892,370.043 41.0015,370.044 41.0139,370.045 41.0263,370.046 41.0386,370.047 41.051,370.048 41.0634,370.049 41.0757,370.05 41.0881,370.051 
 41.1005,370.052 41.1128,370.053 41.1252,370.054 41.1376,370.055 41.1499,370.056 41.1623,370.057 41.1747,370.058 41.187,370.059 41.1994,370.06 41.2118,370.06 
 41.2242,370.061 41.2365,370.062 41.2489,370.063 41.2613,370.064 41.2736,370.065 41.286,370.066 41.2984,370.067 41.3107,370.068 41.3231,370.068 41.3355,370.069 
 41.3478,370.07 41.3602,370.071 41.3726,370.072 41.3849,370.073 41.3973,370.073 41.4097,370.074 41.4221,370.075 41.4344,370.076 41.4468,370.077 41.4592,370.077 
 41.4715,370.078 41.4839,370.079 41.4963,370.08 41.5086,370.08 41.521,370.081 41.5334,370.082 41.5457,370.083 41.5581,370.083 41.5705,370.084 41.5828,370.085 
 41.5952,370.085 41.6076,370.086 41.6199,370.087 41.6323,370.087 41.6447,370.088 41.6571,370.089 41.6694,370.089 41.6818,370.09 41.6942,370.091 41.7065,370.091 
 41.7189,370.092 41.7313,370.092 41.7436,370.093 41.756,370.093 41.7684,370.094 41.7807,370.095 41.7931,370.095 41.8055,370.096 41.8178,370.096 41.8302,370.097 
 41.8426,370.097 41.8549,370.098 41.8673,370.098 41.8797,370.099 41.8921,370.099 41.9044,370.1 41.9168,370.1 41.9292,370.101 41.9415,370.101 41.9539,370.101 
 41.9663,370.102 41.9786,370.102 41.991,370.103 42.0034,370.103 42.0157,370.103 42.0281,370.104 42.0405,370.104 42.0528,370.105 42.0652,370.105 42.0776,370.105 
 42.0899,370.106 42.1023,370.106 42.1147,370.106 42.1271,370.107 42.1394,370.107 42.1518,370.107 42.1642,370.107 42.1765,370.108 42.1889,370.108 42.2013,370.108 
 42.2136,370.109 42.226,370.109 42.2384,370.109 42.2507,370.109 42.2631,370.11 42.2755,370.11 42.2878,370.11 42.3002,370.11 42.3126,370.11 42.325,370.111 
 42.3373,370.111

In [126]:
plot(iNa,label = "INa")
plot!(iK,label = "IK")
plot!(iL,label = "IL")

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 10000 
 
 
 20000 
 
 
 30000 
 
 
 40000 
 
 
 -500 
 
 
 0 
 
 
 500 
 
<polyline clip-path="url(#clip02)" style="stroke:#0099ff; stroke-width:0.8; stroke-opacity:1; fill:none" points="
 39.4926,202.412 39.5049,202.413 39.5173,202.415 39.5297,202.417 39.542,202.418 39.5544,202.42 39.5668,202.421 39.5791,202.422 39.5915,202.423 39.6039,202.425 
 39.6162,202.426 39.6286,202.427 39.641,202.428 39.6534,202.429 39.6657,202.43 39.6781,202.431 39.6905,202.432 39.7028,202.433 39.7152,202.433 39.7276,202.434 
 39.7399,202.435 39.7523,202.435 39.7647,202.436 39.777,202.437 39.7894,202.437 39.8018,202.438 39.8141,202.438 39.8265,202.439 39.8389,202.439 39.8513,202.44 
 39.8636,202.44 39.876,202.441 39.8884,202.441 39.9007,202.441 39.9131,202.442 39.9255,202.442 39.9378,202.442 39.9502,202.443 39.9626,202.443 39.9749,202.443 
 39.9873,202.443 39.9997,202.444 40.012,202.444 40.0244,202.444 40.0368,202.444 40.0491,202.444 40.0615,202.444 40.0739,202.445 40.0863,202.445 40.0986,202.445 
 40.111,202.445 40.1234,202.445 40.1357,202.445 40.1481,202.445 40.1605,202.445 40.1728,202.445 40.1852,202.446 40.1976,202.446 40.2099,202.446 40.2223,202.446 
 40.2347,202.446 40.247,202.446 40.2594,202.446 40.2718,202.446 40.2841,202.446 40.2965,202.446 40.3089,202.446 40.3213,202.446 40.3336,202.446 40.346,202.446 
 40.3584,202.446 40.3707,202.446 40.3831,202.446 40.3955,202.446 40.4078,202.446 40.4202,202.446 40.4326,202.446 40.4449,202.446 40.4573,202.446 40.4697,202.446 
 40.482,202.446 40.4944,202.446 40.5068,202.446 40.5191,202.446 40.5315,202.446 40.5439,202.446 40.5563,202.446 40.5686,202.446 40.581,202.446 40.5934,202.446 
 40.6057,202.446 40.6181,202.446 40.6305,202.446 40.6428,202.446 40.6552,202.446 40.6676,202.446 40.6799,202.446 40.6923,202.446 40.7047,202.445 40.717,202.445 
 40.7294,202.445 40.7418,202.445 40.7542,202.445 40.7665,202.445 40.7789,202.445 40.7913,202.445 40.8036,202.445 40.816,202.445 40.8284,202.445 40.8407,202.445 
 40.8531,202.445 40.8655,202.445 40.8778,202.445 40.8902,202.445 40.9026,202.445 40.9149,202.445 40.9273,202.445 40.9397,202.445 40.952,202.445 40.9644,202.445 
 40.9768,202.445 40.9892,202.445 41.0015,202.445 41.0139,202.445 41.0263,202.444 41.0386,202.444 41.051,202.444 41.0634,202.444 41.0757,202.444 41.0881,202.444 
 41.1005,202.444 41.1128,202.444 41.1252,202.444 41.1376,202.444 41.1499,202.444 41.1623,202.444 41.1747,202.444 41.187,202.444 41.1994,202.444 41.2118,202.444 
 41.2242,202.444 41.2365,202.444 41.2489,202.444 41.2613,202.444 41.2736,202.444 41.286,202.444 41.2984,202.444 41.3107,202.444 41.3231,202.444 41.3355,202.444 
 41.3478,202.444 41.3602,202.444 41.3726,202.443 41.3849,202.443 41.3973,202.443 41.4097,202.443 41.4221,202.443 41.4344,202.443 41.4468,202.443 41.4592,202.443 
 41.4715,202.443 41.4839,202.443 41.4963,202.443 41.5086,202.443 41.521,202.443 41.5334,202.443 41.5457,202.443 41.5581,202.443 41.5705,202.443 41.5828,202.443 
 41.5952,202.443 41.6076,202.443 41.6199,202.443 41.6323,202.443 41.6447,202.443 41.6571,202.443 41.6694,202.443 41.6818,202.443 41.6942,202.443 41.7065,202.443 
 41.7189,202.443 41.7313,202.443 41.7436,202.443 41.756,202.443 41.7684,202.443 41.7807,202.443 41.7931,202.443 41.8055,202.443 41.8178,202.443 41.8302,202.443 
 41.8426,202.443 41.8549,202.442 41.8673,202.442 41.8797,202.442 41.8921,202.442 41.9044,202.442 41.9168,202.442 41.9292,202.442 41.9415,202.442 41.9539,202.442 
 41.9663,202.442 41.9786,202.442 41.991,202.442 42.0034,202.442 42.0157,202.442 42.0281,202.442 42.0405,202.442 42.0528,202.442 42.0652,202.442 42.0776,202.442 
 42.0899,202.442 42.1023,202.442 42.1147,202.442 42.1271,202.442 42.1394,202.442 42.1518,202.442 42.1642,202.442 42.1765,202.442 42.1889,202.442 42.2013,202.442 
 42.2136,202.442 42.226,202.442 42.2384,202.442 42.2507,202.442 42.2631,202.442 42.2755,202.442 42.2878,202.442 42.3002,202.442 42.3126,202.442 42.325,202.442 
 